In [1]:
import torch 
from torch import nn

import ray
from ray.rllib.agents import ppo
from ray.rllib.models import ModelCatalog
from ray.rllib.models.torch.torch_modelv2 import TorchModelV2
from ray.rllib.utils.annotations import override

#from models import VisualEncoder
from train import *
from wrappers_2 import *

/root/miniconda/envs/py37/lib/python3.7/site-packages/gym/logger.py:30: UserWarning: WARN: Box bound precision lowered by casting to float32
  warnings.warn(colorize('%s: %s'%('WARN', msg % args), 'yellow'))


In [2]:
class VisualEncoder(nn.Module):
    def __init__(self):
        super().__init__()

        self.cnn = nn.Sequential(
            nn.Conv2d(3, 32, kernel_size=2, stride=2, padding=0),  
            nn.ELU(),
            nn.Conv2d(32, 32, kernel_size=2, stride=2, padding=0), 
            nn.ELU(),
            nn.Conv2d(32, 64, kernel_size=2, stride=2, padding=0), 
            nn.ELU(),
            nn.Conv2d(64, 128, kernel_size=2, stride=2, padding=0),
            nn.ELU(), 
            nn.Conv2d(128, 256, kernel_size=2, stride=2, padding=0),
            nn.ELU(),
            nn.Conv2d(256, 512, kernel_size=2, stride=2, padding=0),
            nn.ELU(),
            nn.Flatten(),
        )

    def forward(self, x):
        return self.cnn(x)

In [3]:
from torch.nn.functional import one_hot

class MyModelClass(TorchModelV2, nn.Module):
    def __init__(self, obs_space, action_space, num_outputs, model_config, name):
        TorchModelV2.__init__(self, obs_space, action_space, num_outputs, model_config, name)
        nn.Module.__init__(self)
        visual_features_dim = 512
        target_features_dim = 9 * 11 * 11 
        self.visual_encoder = VisualEncoder()
        self.visual_encoder.load_state_dict(
            torch.load("/IGLU-Minecraft/models/AngelaCNN/encoder_weigths.pth", map_location=torch.device('cpu'))
        )
        self.target_encoder = nn.Sequential(
            nn.Conv3d(7, 1, kernel_size=1, stride=1, padding=0),
            nn.ELU(),
        )
        policy_hidden_dim = 256 
        self.policy_network = nn.Sequential(
            nn.Linear(visual_features_dim + target_features_dim, 1024),
            nn.ELU(),
            nn.Linear(1024, 512),
            nn.ELU(),
            nn.Linear(512, policy_hidden_dim),
            nn.ELU(),
            nn.Linear(policy_hidden_dim, policy_hidden_dim),
            nn.ELU(),
            #nn.Linear(policy_hidden_dim, policy_hidden_dim),
            #nn.ELU(),
        )
        self.action_head = nn.Linear(policy_hidden_dim, action_space.n)
        self.value_head = nn.Linear(policy_hidden_dim, 1)
        self.last_value = None
        
        self.use_cuda = torch.cuda.is_available()
        if self.use_cuda:
            self.visual_encoder.cuda()
            self.target_encoder.cuda()
            self.policy_network.cuda()
            self.action_head.cuda()
            self.value_head.cuda()
        
    @override(TorchModelV2)
    def forward(self, input_dict, state, seq_lens):
        obs = input_dict['obs']
        pov = obs['pov'].permute(0, 3, 1, 2).float() / 255.0
        target = one_hot(obs['target_grid'].long(), num_classes=7).permute(0, 4, 1, 2, 3).float()
        if self.use_cuda:
            pov.cuda()
            target.cuda()
            
        with torch.no_grad():
            visual_features = self.visual_encoder(pov)
            
        target_features = self.target_encoder(target)
        target_features = target_features.reshape(target_features.shape[0], -1)
        features = torch.cat([visual_features, target_features], dim=1)
        features = self.policy_network(features)
        action = self.action_head(features)
        self.last_value = self.value_head(features).squeeze(1)
        return action, state
    
    @override(TorchModelV2)
    def value_function(self):
        assert self.last_value is not None, "must call forward() first"
        return self.last_value

In [4]:
ModelCatalog.register_custom_model("my_torch_model", MyModelClass)

In [5]:
class VisualObservationWrapper(ObsWrapper):
    def __init__(self, env, include_target=False):
        super().__init__(env)
        self.observation_space = {   
            'pov': gym.spaces.Box(low=0, high=255, shape=(64, 64, 3)),
            'inventory': gym.spaces.Box(low=0.0, high=20.0, shape=(6,)),
            'compass': gym.spaces.Box(low=-180.0, high=180.0, shape=(1,))
        }
        if include_target:
            self.observation_space['target_grid'] = \
                gym.spaces.Box(low=0, high=6, shape=(9, 11, 11))
        self.observation_space = gym.spaces.Dict(self.observation_space)

    def observation(self, obs, reward=None, done=None, info=None):
        if info is not None:
            if 'target_grid' in info:
                target_grid = info['target_grid']
                del info['target_grid']
            else:
                logger.error(f'info: {info}')
                if hasattr(self.unwrapped, 'should_reset'):
                    self.unwrapped.should_reset(True)
                target_grid = self.env.unwrapped.tasks.current.target_grid
        else:
            target_grid = self.env.unwrapped.tasks.current.target_grid
        return {
            'pov': obs['pov'].astype(np.float32),
            'inventory': obs['inventory'],
            'compass': np.array([obs['compass']['angle'].item()]),
            'target_grid': target_grid
        }

In [6]:
import os
os.environ["CUDA_DEVICE_ORDER"]="PCI_BUS_ID"   # see issue #152
os.environ["CUDA_VISIBLE_DEVICES"]="0"

class RewardWrapper(gym.RewardWrapper):
    def __init__(self, env):
        super().__init__(env)
    
    def reward(self, rew):
        if rew == 0:
            rew = -0.1
        return rew
    
def env_creator(env_config):
    env = gym.make('IGLUSilentBuilder-v0', max_steps=1000)
    env.update_taskset(TaskSet(preset=['C3', 'C17', 'C32']))
    #env = PovOnlyWrapper(env)
    env = VisualObservationWrapper(env, include_target=True)
    env = SelectAndPlace(env)
    env = Discretization(env, flat_action_space('human-level'))
    env = RewardWrapper(env)
    return env

from ray.tune.registry import register_env
register_env("my_env", env_creator)

from ray import tune
from ray.rllib.agents.ppo import PPOTrainer

In [7]:
from ray.tune.integration.wandb import WandbLogger

analysis = tune.run(PPOTrainer, 
         config={
             "env": "my_env", 
             "framework": "torch",
             "num_gpus": 1,
             "num_workers": 1,
             "sgd_minibatch_size": 256,
             "clip_param": 0.2,
             "entropy_coeff": 0.01,
             "lambda": 0.95,
             "train_batch_size": 1000,
             #"gamma": 0.99,
             "model": {
                    # Specify our custom model from above.
                    "custom_model": "my_torch_model",
                    # Extra kwargs to be passed to your model's c'tor.
                    "custom_model_config": {},
              },
             "logger_config": {
                  "wandb": {
                      "project": "IGLU-Minecraft",
                      "name": "PPO MultiTask (C3, C17, C32) pretrained (AngelaCNN) (3 noops after placement) r: -0.1"
                  }
              }

        },
        loggers=[WandbLogger],
        checkpoint_at_end=True)

/root/miniconda/envs/py37/lib/python3.7/site-packages/ray/_private/services.py:238: UserWarning: Not all Ray Dashboard dependencies were found. To use the dashboard please install Ray using `pip install ray[default]`. To disable this message, set RAY_DISABLE_IMPORT_WARNING env var to '1'.
  warnings.warn(warning_message)


2021-10-28 21:05:50,841	INFO wandb.py:170 -- Already logged into W&B.
2021-10-28 21:05:50,851	ERROR syncer.py:72 -- Log sync requires rsync to be installed.
wandb: Currently logged in as: linar (use `wandb login --relogin` to force relogin)
wandb: WARNING Tried to auto resume run with id a93f6_00000 but id d4877_00000 is set.
wandb: wandb version 0.12.6 is available!  To upgrade, please run:
wandb:  $ pip install wandb --upgrade
(pid=154) /root/miniconda/envs/py37/lib/python3.7/site-packages/gym/logger.py:30: UserWarning: WARN: Box bound precision lowered by casting to float32
(pid=154)   warnings.warn(colorize('%s: %s'%('WARN', msg % args), 'yellow'))


(pid=154) 2021-10-28 21:05:54,378	INFO ppo.py:159 -- In multi-agent mode, policies will be optimized sequentially by the multi-GPU optimizer. Consider setting simple_optimizer=True if this doesn't work for you.
(pid=154) 2021-10-28 21:05:54,378	INFO trainer.py:728 -- Current log_level is WARN. For more information, set 'log_level': 'INFO' / 'DEBUG' or use the -v and -vv flags.
(pid=146) /root/miniconda/envs/py37/lib/python3.7/site-packages/gym/logger.py:30: UserWarning: WARN: Box bound precision lowered by casting to float32
(pid=146)   warnings.warn(colorize('%s: %s'%('WARN', msg % args), 'yellow'))
(pid=154) 2021-10-28 21:06:00,414	WARNING util.py:55 -- Install gputil for GPU system monitoring.
(pid=146) /root/miniconda/envs/py37/lib/python3.7/site-packages/gym/logger.py:30: UserWarning: WARN: Box bound precision lowered by casting to float32
(pid=146)   warnings.warn(colorize('%s: %s'%('WARN', msg % args), 'yellow'))
(pid=146) /root/miniconda/envs/py37/lib/python3.7/site-packages/gy

Result for PPO_my_env_d4877_00000:
  agent_timesteps_total: 1000
  custom_metrics: {}
  date: 2021-10-28_21-07-08
  done: false
  episode_len_mean: 416.0
  episode_media: {}
  episode_reward_max: -40.1000000000003
  episode_reward_mean: -41.60000000000032
  episode_reward_min: -43.10000000000034
  episodes_this_iter: 2
  episodes_total: 2
  experiment_id: ab3163f264094146aa0559df77a991b6
  hostname: b53f0c0cd556
  info:
    learner:
      default_policy:
        learner_stats:
          cur_kl_coeff: 0.19999999999999996
          cur_lr: 5.000000000000001e-05
          entropy: 2.88278742896186
          entropy_coeff: 0.009999999999999998
          kl: 0.007874982552508255
          policy_loss: 0.06394314674867524
          total_loss: 0.23382639065384864
          vf_explained_var: 0.011645793914794922
          vf_loss: 0.19713611917363272
    num_agent_steps_sampled: 1000
    num_agent_steps_trained: 1000
    num_steps_sampled: 1000
    num_steps_trained: 1000
  iterations_since_r

Result for PPO_my_env_d4877_00000:
  agent_timesteps_total: 2000
  custom_metrics: {}
  date: 2021-10-28_21-07-42
  done: false
  episode_len_mean: 399.0
  episode_media: {}
  episode_reward_max: -36.900000000000254
  episode_reward_mean: -40.5000000000003
  episode_reward_min: -43.10000000000034
  episodes_this_iter: 3
  episodes_total: 5
  experiment_id: ab3163f264094146aa0559df77a991b6
  hostname: b53f0c0cd556
  info:
    learner:
      default_policy:
        learner_stats:
          cur_kl_coeff: 0.19999999999999996
          cur_lr: 5.000000000000001e-05
          entropy: 2.86048350599077
          entropy_coeff: 0.009999999999999998
          kl: 0.010376032421635392
          policy_loss: 0.025860504930218062
          total_loss: 0.6812869512372547
          vf_explained_var: 0.04848691076040268
          vf_loss: 0.6819560726897584
    num_agent_steps_sampled: 2000
    num_agent_steps_trained: 2000
    num_steps_sampled: 2000
    num_steps_trained: 2000
  iterations_since_re

...

Result for PPO_my_env_d4877_00000:
  agent_timesteps_total: 1845000
  custom_metrics: {}
  date: 2021-10-29_10-54-02
  done: false
  episode_len_mean: 289.35
  episode_media: {}
  episode_reward_max: -19.70000000000001
  episode_reward_mean: -28.935000000000144
  episode_reward_min: -49.80000000000044
  episodes_this_iter: 3
  episodes_total: 6147
  experiment_id: ab3163f264094146aa0559df77a991b6
  hostname: b53f0c0cd556
  info:
    learner:
      default_policy:
        learner_stats:
          cur_kl_coeff: 0.5196265840650668
          cur_lr: 5.000000000000001e-05
          entropy: 1.3750950031810336
          entropy_coeff: 0.009999999999999998
          kl: 0.004638684191440332
          policy_loss: 0.07223363154464298
          total_loss: 0.7846143325169881
          vf_explained_var: 0.4913325905799866
          vf_loss: 0.7237212768859334
    num_agent_steps_sampled: 1845000
    num_agent_steps_trained: 1845000
    num_steps_sampled: 1845000
    num_steps_trained: 1845000
  

(pid=146) /root/miniconda/envs/py37/lib/python3.7/site-packages/gym/logger.py:30: UserWarning: WARN: Box bound precision lowered by casting to float32
(pid=146)   warnings.warn(colorize('%s: %s'%('WARN', msg % args), 'yellow'))


Result for PPO_my_env_d4877_00000:
  agent_timesteps_total: 1846000
  custom_metrics: {}
  date: 2021-10-29_10-54-45
  done: false
  episode_len_mean: 289.71
  episode_media: {}
  episode_reward_max: -19.70000000000001
  episode_reward_mean: -28.971000000000146
  episode_reward_min: -49.80000000000044
  episodes_this_iter: 3
  episodes_total: 6150
  experiment_id: ab3163f264094146aa0559df77a991b6
  hostname: b53f0c0cd556
  info:
    learner:
      default_policy:
        learner_stats:
          cur_kl_coeff: 0.2598132920325334
          cur_lr: 5.000000000000001e-05
          entropy: 1.3577826698621114
          entropy_coeff: 0.009999999999999998
          kl: 0.016187203700055896
          policy_loss: 0.0030262505014737448
          total_loss: 0.711601487464375
          vf_explained_var: 0.14819279313087463
          vf_loss: 0.7179474050800005
    num_agent_steps_sampled: 1846000
    num_agent_steps_trained: 1846000
    num_steps_sampled: 1846000
    num_steps_trained: 1846000


2021-10-29 10:55:08,419	WARNING tune.py:519 -- SIGINT received (e.g. via Ctrl+C), ending Ray Tune run. This will try to checkpoint the experiment state one last time. Press CTRL+C one more time (or send SIGINT/SIGKILL/SIGTERM) to skip. 
2021-10-29 10:55:08,419	WARNING tune.py:519 -- SIGINT received (e.g. via Ctrl+C), ending Ray Tune run. This will try to checkpoint the experiment state one last time. Press CTRL+C one more time (or send SIGINT/SIGKILL/SIGTERM) to skip. 
2021-10-29 10:55:08,485	WARNING tune.py:519 -- SIGINT received (e.g. via Ctrl+C), ending Ray Tune run. This will try to checkpoint the experiment state one last time. Press CTRL+C one more time (or send SIGINT/SIGKILL/SIGTERM) to skip. 
Process _WandbLoggingProcess-1:
Traceback (most recent call last):
  File "/root/miniconda/envs/py37/lib/python3.7/multiprocessing/process.py", line 297, in _bootstrap
    self.run()
  File "/root/miniconda/envs/py37/lib/python3.7/site-packages/ray/tune/integration/wandb.py", line 200, in

KeyboardInterrupt: 